## Stream Processing Arquitectura Completa

Goals:

* Perform a realtime stock prices analytics
* For this we use two data sources
    * [IEX Cloud](https://iexcloud.io/)
    * [Twitter](https://developer.twitter.com/)
* We implement following data pipeline
    * Data Ingestion in Nifi and Kafka
    * Data processing with Spark Streaming
    * Data Storage on Elasticsearch
    * Data visualization on Kibana


Let’s create a data processing for Stock prices

In [1]:
import sys
import json
import pprint
from pyspark import SparkContext
from pyspark import SparkConf
from pyspark.streaming import StreamingContext

from pyspark.streaming.kafka import KafkaUtils

conf = SparkConf().setAll([("es.index.auto.create", "true")])

sc = SparkContext(appName="QuotesConsumer",conf=conf)
ssc = StreamingContext(sc, 1)

kafkaParams = {'bootstrap.servers': 'broker:29092', 'group.id' : 'quotesConsumer'}
topicQuotes = ['quotes']

streamQuotes = KafkaUtils.createDirectStream(ssc, topicQuotes, kafkaParams)

Load companies Json reference on a dictionary

In [3]:
with open('companies.json') as json_file:
    Lines = json_file.readlines()
    
companies = { }
# Parse compnies data
for line in Lines: 
    data = json.loads(line) 
    companies[data["symbol"]]=data

Create an enrichment function to add company data to every input quote
    
    


In [4]:
def enrichQuote(quote, companies):
    quoteJson=json.loads(quote[1])    
    companyJson=companies[quoteJson["symbol"]]
    quoteJson.update(companyJson) 
    return(quote[0],json.dumps(quoteJson))

Now apply a map to add this company reference fields

In [5]:
streamQuotesEnriched=streamQuotes.map(lambda record : enrichQuote(record,companies) )                                   
    
streamQuotesEnriched.map(lambda record : (record[0], record[1])).pprint()

Finally we add a sink to store on elastic

In [6]:
es_write_quotes = {
        "es.nodes" : "elasticsearch",
        "es.port" : "9200",
        "es.resource" : 'quotes/_doc',
        "es.input.json": "yes",
    }


streamQuotesEnriched.foreachRDD(lambda rdd: rdd.saveAsNewAPIHadoopFile(
        path='-',
        outputFormatClass="org.elasticsearch.hadoop.mr.EsOutputFormat",
        keyClass="org.apache.hadoop.io.NullWritable",
        valueClass="org.elasticsearch.hadoop.mr.LinkedMapWritable",
        conf=es_write_quotes))

Let’s create a data processing for twitter

In [7]:
topicTwitter = ['tweets']

streamTwitter = KafkaUtils.createDirectStream(ssc, topicTwitter, kafkaParams)

streamTwitter.map(lambda record : (record[0], record[1])).pprint()


es_write_twitter = {
        "es.nodes" : "elasticsearch",
        "es.port" : "9200",
        "es.resource" : 'tweets/_doc',
        "es.input.json": "yes",
    }

streamTwitter.foreachRDD(lambda rdd: rdd.saveAsNewAPIHadoopFile(
        path='-',
        outputFormatClass="org.elasticsearch.hadoop.mr.EsOutputFormat",
        keyClass="org.apache.hadoop.io.NullWritable",
        valueClass="org.elasticsearch.hadoop.mr.LinkedMapWritable",
        conf=es_write_twitter))

Finally let's launch the process

In [8]:

ssc.start()
ssc.awaitTermination()

-------------------------------------------
Time: 2021-01-28 19:47:20
-------------------------------------------
(None, '{"symbol": "ORCL", "companyName": "Oracle Corp.", "primaryExchange": "K EO WKC ICNNEGR,XYTE H.NSOAC", "calculationPrice": "tops", "open": null, "openTime": null, "openSource": "affoliic", "close": null, "closeTime": null, "closeSource": "fiifcaol", "high": null, "highTime": 1662764808749, "highSource": "pri cm e aeule5n1ydteid", "low": null, "lowTime": 1678126005374, "lowSource": "ieaitmeeplXc  r ErI", "latestPrice": 62.05, "latestSource": "IEX real time price", "latestTime": "2:45:57 PM", "latestUpdate": 1654860939426, "latestVolume": null, "iexRealtimePrice": 64.47, "iexRealtimeSize": 100, "iexLastUpdated": 1638699268568, "delayedPrice": null, "delayedPriceTime": null, "oddLotDelayedPrice": null, "oddLotDelayedPriceTime": null, "extendedPrice": null, "extendedChange": null, "extendedChangePercent": null, "extendedPriceTime": null, "previousClose": 64.26, "previous

-------------------------------------------
Time: 2021-01-28 19:47:20
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:21
-------------------------------------------
(None, '{"symbol": "AAPL", "companyName": "Apple, Inc.", "primaryExchange": "NGAETACE SL/ASBADO T()NEQMKSL GLR", "calculationPrice": "tops", "open": null, "openTime": null, "openSource": "fcoiilaf", "close": null, "closeTime": null, "closeSource": "ficilfao", "high": null, "highTime": null, "highSource": null, "low": null, "lowTime": null, "lowSource": null, "latestPrice": 143.06, "latestSource": "IEX real time price", "latestTime": "2:47:10 PM", "latestUpdate": 1670968660103, "latestVolume": null, "iexRealtimePrice": 143.06, "iexRealtimeSize": 94, "iexLastUpdated": 1637892177766, "delayedPrice": null, "delayedPriceTime": null, "oddLotDelayedPrice": null, "oddLotDelayedPriceTime": null, "extendedPrice": null, "extendedChange": null, "extendedChangePercent": nul

-------------------------------------------
Time: 2021-01-28 19:47:36
-------------------------------------------
(None, '{"symbol": "ORCL", "companyName": "Oracle Corp.", "primaryExchange": "WE.NSGI CR TEKKOCN O XHE,CYAN", "calculationPrice": "tops", "open": null, "openTime": null, "openSource": "fcilaifo", "close": null, "closeTime": null, "closeSource": "falifoic", "high": null, "highTime": 1688451305490, "highSource": "ul d5eneecyme1a  diitpr", "low": null, "lowTime": 1673948765517, "lowSource": "IXtiercle m aiEr ep", "latestPrice": 63.525, "latestSource": "IEX real time price", "latestTime": "2:47:15 PM", "latestUpdate": 1658871063653, "latestVolume": null, "iexRealtimePrice": 64.247, "iexRealtimeSize": 10, "iexLastUpdated": 1617703599097, "delayedPrice": null, "delayedPriceTime": null, "oddLotDelayedPrice": null, "oddLotDelayedPriceTime": null, "extendedPrice": null, "extendedChange": null, "extendedChangePercent": null, "extendedPriceTime": null, "previousClose": 63.4, "previous

-------------------------------------------
Time: 2021-01-28 19:47:50
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:50
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:51
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:51
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:52
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:52
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:53
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:53
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:54
----------

-------------------------------------------
Time: 2021-01-28 19:47:58
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:58
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:59
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 19:47:59
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 19:47:46 +0000 2021","id":1354878857229135873,"id_str":"1354878857229135873","text":"RT @rachelbovard: Google is now censoring Senate testimony, given under oath.","source":"\\u003ca href=\\"http:\\/\\/twitter.com\\/download\\/iphone\\" rel=\\"nofollow\\"\\u003eTwitter for iPhone\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":20959042,"id_str":"209590

...

-------------------------------------------
Time: 2021-01-28 20:01:57
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:01:57
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 20:01:45 +0000 2021","id":1354882373939302403,"id_str":"1354882373939302403","text":"I got tired of people texting me asking me how to do this and that. Ask Google, because ppl want information from m\\u2026 https:\\/\\/t.co\\/KpZFye4K3o","source":"\\u003ca href=\\"http:\\/\\/twitter.com\\/download\\/iphone\\" rel=\\"nofollow\\"\\u003eTwitter for iPhone\\u003c\\/a\\u003e","truncated":true,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":3003999354,"id_str":"3003999354","name":"Tianna Jenkins","screen_name":"flourishblkgirl","location":"Spring, TX","url":"https:\\/\\/msha.ke\\/tiannajenkins\\/","description":"Christ

-------------------------------------------
Time: 2021-01-28 20:01:59
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:01:59
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 20:01:46 +0000 2021","id":1354882379018547208,"id_str":"1354882379018547208","text":"Google your name + pirate aesthetic outfit, ship, and weapon  \\n\\n\\ud83d\\udc40\\ud83d\\udc40\\ud83d\\udc40 https:\\/\\/t.co\\/6ZXfnZZVTK","display_text_range":[0,67],"source":"\\u003ca href=\\"http:\\/\\/twitter.com\\/download\\/iphone\\" rel=\\"nofollow\\"\\u003eTwitter for iPhone\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":2447632069,"id_str":"2447632069","name":"marty \\ud83c\\udf08 1312","screen_name":"marty_mcbi","location":"Austin, TX","url":"https:\\/\\/open.spotify.com\\/user\\/

-------------------------------------------
Time: 2021-01-28 20:02:00
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:02:00
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:02:01
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:02:01
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 20:01:48 +0000 2021","id":1354882388061515779,"id_str":"1354882388061515779","text":"RT @philthatremains: Robinhood \\"Let the people trade\\"\\n\\nGoogle \\"Don\'t be evil\\"\\n\\nTwitter \\"The free speech wing of the free speech party\\"\\n\\nThe\\u2026","source":"\\u003ca href=\\"http:\\/\\/twitter.com\\/download\\/android\\" rel=\\"nofollow\\"\\u003eTwitter for Android\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_

-------------------------------------------
Time: 2021-01-28 20:02:02
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:02:02
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 20:01:49 +0000 2021","id":1354882393098883074,"id_str":"1354882393098883074","text":"Google\\u2019s \\u2018Clearly White\\u2019 Pixel 4a 5G is now available in Canada https:\\/\\/t.co\\/SQPIH8d34R","source":"\\u003ca href=\\"https:\\/\\/ifttt.com\\" rel=\\"nofollow\\"\\u003eIFTTT\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":903242772,"id_str":"903242772","name":"Aderoju Adelere","screen_name":"AderojuAdelere","location":"Lagos, Nigeria","url":"http:\\/\\/www.aderojuadelere.com.ng","description":"Aderoju Adelere is an IT Consultant, Engineer, Professional Web\\/Mobile Entrepr

-------------------------------------------
Time: 2021-01-28 20:02:04
-------------------------------------------

-------------------------------------------
Time: 2021-01-28 20:02:04
-------------------------------------------
(None, '{"created_at":"Thu Jan 28 20:01:51 +0000 2021","id":1354882400929669120,"id_str":"1354882400929669120","text":"Scala, React and.. Google Spreadsheets? Awesome mixed code\\/no-code approach from The Guardian team.\\n\\nhttps:\\/\\/t.co\\/xkyzcwsP8x","source":"\\u003ca href=\\"http:\\/\\/twitter.com\\/download\\/android\\" rel=\\"nofollow\\"\\u003eTwitter for Android\\u003c\\/a\\u003e","truncated":false,"in_reply_to_status_id":null,"in_reply_to_status_id_str":null,"in_reply_to_user_id":null,"in_reply_to_user_id_str":null,"in_reply_to_screen_name":null,"user":{"id":171462019,"id_str":"171462019","name":"Andrey Salomatin","screen_name":"flpvsk","location":null,"url":"http:\\/\\/flpvsk.com","description":"boards \\u2022 polyrhythms \\u2022 @podcastcode \\u20